# PROGRAMA DE CIENCIAS DE LOS DATOS 
# **Curso: Big Data**
## **PROYECTO FINAL:**

## <font color='red'>Streaming de tendencias con #hashtags en Twitter</font>. 
## <font color='blue'>Parte 1: Conexión con API TWITTER + APACHE SPARK</font>. 

#### **Profesor: MSc. Felipe Meza Obando**


#### Alumnos: 
  
####  **Lester Salazar Viales.**
####  **Randal Salazar Viales.**

Este proyecto permite mediante una aplicación simple, leer transmisiones online de Twitter usando Python, luego procesa los tweets usando Apache Spark Streaming para identificar los campos de los tweets definidos y finalmente, regresa los hashtags que están de tendencia en ese momento (tiempo real).

### Instalación de Libería empleada: <font color='blue'>Tweepy</font>.

Para lograr la conexión API entre la máquina local y la API TWITTER, se empleó el paquete Tweey.

Este librería de Python es de fácil uso para lograr accesar la API TWITTER.

El comando de instalación de la misma para conda es:

**conda install -c conda-forge tweepy**

## Paso 1: <font color='blue'>Creación de las Credenciales Propios para las API de Twitter</font>.

Se asume para efectos de la notebook, que este paso ya fue efectuado (si desea conocer como efectuarlo, revisar el documento pdf entregable del proyecto)

## Paso 2: <font color='blue'>Construcción de Cliente API de Twitter</font>.

Construcción de un cliente simple que obtendrá los tweets de la API de Twitter usando Python, y éste pasará los tweets a la instancia de **Spark Streaming**.

### **Importación de Librerías** a ser utilizadas para la conexión al cliente API.

In [1]:
import os
import tweepy
from tweepy import OAuthHandler
from tweepy import Stream
from tweepy.streaming import StreamListener
import socket
import json
import preprocessor as p

### Variables Token / Keys generadas por la API TWITTER para poder conectarse a TWITTER

Definición de las varibales de autenticación Key/Token, requeridas por la API TWITTER para poder conectarse a esta aplicación. Las variables son dadas por la API TWITTER.

In [2]:
CONSUMER_KEY='gXokQgEW6dv8fSSnKTvvxL2qg'
CONSUMER_SECRET='a2jOnasE5sgnh2UfVDY1izwHuzoaOPIjGWCVFBXnLdnfkqZi7n'
ACCESS_TOKEN ='1224205344257335297-BY4usKicNvYTEPjA6uBPiGlumA32Mf'
ACCESS_TOKEN_SECRET='RdzJYaqFF2FWS6ZmndlJr8l8v35r6uTFbLxQwChKHHDY4'

auth = tweepy.OAuthHandler(CONSUMER_KEY, CONSUMER_SECRET)
auth.set_access_token(ACCESS_TOKEN, ACCESS_TOKEN_SECRET)

### Definición de Clase para escuchar mensajes de TWITTER mediante la API TWITTER

El objetivo de definir una clase, es poder definir para el mensaje obtenido mediante la API TWITTER, el formato con el cuál se enviará el Stream hacia Apache Spark para poder efectuar el análisis de streaming correspondiente.

Para poder verificar que se envía el mensaje con los campos definidos a ser recibidos en Spark, se decide imprimir en pantalla ambos mensajes: mensaje TWITTER y el mensaje a enviar a Streaming, lo que permite comprobar que se a mapeado correctamente los campos.

In [3]:
class MyStreamListener(tweepy.StreamListener):
    
    def __init__(self, csocket):
        self.client_socket = csocket

    def on_data(self, raw_data):
        try:
            # Variable con los datos completos obtenidos desde TWITTER
            tweets = json.loads(raw_data)
            
            # Definición de campos del mensaje de TWITTER a enviar para Streaming
            if 'extended_tweet' not in tweets:
                text = tweets['text'].strip()
            else:
                text = tweets['extended_tweet']['full_text'].strip()
            
            outputMsg = {
                'created_at': tweets['created_at'],
                'text': tweets['text'],
                'userid': tweets['user']['id'],
                'username': tweets['user']['name'],
                'userlocation': tweets['user']['location'],
                'retweet_count': tweets['retweet_count'],
                'entities': [x['text'] for x in tweets['entities']['hashtags']]
            }
            
            # Impresión en pantalla de mensaje TWITTER y el correspondiente mensaje a enviar 
            # hacia la fuente de Análisis Streaming (APache Spark).
            # El poder visualizar ambos datos permite verificar que se esté enviando el mensaje correctamente.
            
            # Impresión en pantalla del tweet de Twitter
            print(' ')
            print(tweets)
            print('****************************************************************** ')
            # Impresión en pantalla del tweet a emplear en el Stream
            print(outputMsg)
            print('------------------------------------------------------------------ ')
            print(' ')
            self.client_socket.send((json.dumps(outputMsg)+'\n').encode('utf-8'))
            return True
        
        except BaseException as e:
            print("Error: " + str(e))
            return True
        
    def on_error(self, status_code):
        print(status_code)
        return True

## Servidor Local de Streams  + Conexión con API Twitter para "escuchar" streams de tweets

- Para poder enviar los mensajes leidos desde la API TWITTER hasta Apache Spark en donde se pretende efectuar el Streaming de datos, se requiere establecer un servidor local tipo Socket. En esta situación, Apache Spark funciona como cliente de este servidor local que obtiene los datos de TWITTER.

- Adicionalmente, se efectúa la conexión entre la API TWITTER y la librería TWEEPY instalada previamente, lo que me permite obtener los datos TWITTER en tiempo real, que podrán ser accesados por Apache Spark mediante la conexión al servido tipo socket definido previamente acá mismo.

In [4]:
import socket
import time

# Conexión de 
#Initializing the port and host
host = 'localhost'
port = 5555
address = (host, port)


#Initializing the socket
server_socket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
server_socket.bind(address)
server_socket.listen(5)

print(server_socket)
print("Listening for client...")

conn, address = server_socket.accept()
print("Connected to Client at " + str(address))


## Conexión con API Twitter para poder "escuchar" streams de los tweets
myStreamListener = MyStreamListener(csocket=conn)
myStream = tweepy.Stream(auth=auth, listener=myStreamListener, )

# Hashtag a buscar en los Tweets:
tracklist = ["#"]
myStream.filter(track=tracklist)

<socket.socket fd=420, family=AddressFamily.AF_INET, type=SocketKind.SOCK_STREAM, proto=0, laddr=('127.0.0.1', 5555)>
Listening for client...
Connected to Client at ('127.0.0.1', 62890)
 
{'created_at': 'Sun Feb 09 21:14:33 +0000 2020', 'id': 1226615393277693955, 'id_str': '1226615393277693955', 'text': 'Blasting Missy Elliott - All N My Grill (Club) right now on Pretty Dope Xperience Radio aka #BlackPandora\n\nlisten n… https://t.co/TGWnuyp0uA', 'source': '<a href="https://radio.co" rel="nofollow">Radio.co now playing</a>', 'truncated': True, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1084627731730464768, 'id_str': '1084627731730464768', 'name': 'Pretty Dope Xperience', 'screen_name': 'XperienceDope', 'location': 'Portland, OR', 'url': 'http://Getpdxradio.com', 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'follow

KeyboardInterrupt: 